# Notebook Configuration

In [18]:
import sys
import re
sys.path.append('/home/rodari78/tesis/CNN_bike_lanes/')

import cv2
import matplotlib.pyplot as plt
import pandas as pd

from libs.YOLO.preprocessing import *
from ultralytics import YOLO

# change base dir
os.chdir('/home/rodari78/tesis/CNN_bike_lanes/app')

Declare paths and constants

In [11]:
# dataset paths
PRM_PATH_ROOT = 'datasets/lima_bike_lanes_subsets'

PRM_PATH_IMG = f'{PRM_PATH_ROOT}/images'
PRM_PATH_LBL = f'{PRM_PATH_ROOT}/labels'
PRM_PATH_GRP = 'labelstudio_output'

# subsets
subsets = ['train', 'val', 'test']

# main files
PRM_YOLO_VERSION = 5
PRM_YOLO_VERSION = str(PRM_YOLO_VERSION).zfill(2)

# declare paths
PRM_BASE_PATH = 'runs/detect'

PRM_VERSION_NAME = f'version_{PRM_YOLO_VERSION}'

PRM_FITTING_PATH = f'{PRM_BASE_PATH}/{PRM_VERSION_NAME}'

PRM_WHOLE_FITTING_PATH = f'/home/rodari78/tesis/CNN_bike_lanes/app/{PRM_FITTING_PATH}'
os.makedirs(PRM_FITTING_PATH, exist_ok = True)

PRM_BEST_MODEL_PATH = f'{PRM_FITTING_PATH}/train/weights/best.pt'

Display summary

In [3]:
summary = pd.Series({'Version': PRM_YOLO_VERSION,
                     'Fitting path': PRM_FITTING_PATH,
                     'Output model': PRM_BEST_MODEL_PATH})\
            .reset_index()\
            .rename(columns = {'index': 'Description',
                               0: 'Values'})

display(summary)

Description                                        Values
0       Version                                            05
1  Fitting path                        runs/detect/version_05
2  Output model  runs/detect/version_05/train/weights/best.pt

Get groups

In [21]:
groups_raw = sorted(os.listdir(PRM_PATH_GRP))
groups_val = [(int(g_r.split('_')[1]), int(g_r.split('_')[2])) for g_r in groups_raw]

Get images

In [30]:
sst_img_lbl = list()
for sst in subsets:
    # get image names
    images = sorted(os.listdir(f'{PRM_PATH_IMG}/{sst}'))

    # get image id
    img_ids = [int(re.findall('[0-9]+', string)[0]) for string in images]

    # search for group
    groups = dict()

    for img_id in img_ids:
        for group_name, (lower_bound, upper_bound) in zip(groups_raw, groups_val):
            if lower_bound <= img_id and img_id <= upper_bound:
                groups[img_id] = group_name
                break

    # validate dictionary
    groups = {id: groups[id] for id in img_ids}

    # get labels from images
    labels = [img.replace('png', 'txt') for img in images]

    # add full path to images
    images = [f'{PRM_PATH_IMG}/{sst}/{img}' for img in images]
    labels = [f'{PRM_PATH_LBL}/{sst}/{lbl}' for lbl in labels]

    # create list of subset
    subset = [sst for _ in range(len(images))]

    # add to main list
    sst_img_lbl.extend(list(zip(list(groups.values()), list(groups.keys()), subset, images, labels)))

Make predictions

In [48]:
def iou(box1, box2):
    # Extract box paramaters
    x1, y1, w1, h1 = box1
    x2, y2, w2, h2 = box2

    # Calculate the corners of the boxes
    x1_min = x1 - w1 / 2
    y1_min = y1 - h1 / 2
    x1_max = x1 + w1 / 2
    y1_max = y1 + h1 / 2
    
    x2_min = x2 - w2 / 2
    y2_min = y2 - h2 / 2
    x2_max = x2 + w2 / 2
    y2_max = y2 + h2 / 2

    # Calculate intersection coordinates
    inter_x_min = max(x1_min, x2_min)
    inter_y_min = max(y1_min, y2_min)
    inter_x_max = min(x1_max, x2_max)
    inter_y_max = min(y1_max, y2_max)

    # Calculate the area of intersection
    inter_width = max(0, inter_x_max - inter_x_min)
    inter_height = max(0, inter_y_max - inter_y_min)
    inter_area = inter_width * inter_height

    # Calculate the area of both boxes
    box1_area = w1 * h1
    box2_area = w2 * h2
    
    # Calculate the IoU
    union_area = box1_area + box2_area - inter_area
    return inter_area / float(union_area) if union_area > 0 else 0

In [40]:
def get_predictions(yolo_result):
    prediction_cls = yolo_result.boxes.cls.cpu().numpy().tolist()
    prediction_box = yolo_result.boxes.xywhn.cpu().numpy().tolist()
    return prediction_cls, prediction_box

In [44]:
def get_ground_truths(path):
    with open(path, 'r') as file:
        labels = file.read()

    labels = [list(map(lambda x: float(x), label.split(' '))) for label in labels.split('\n')[:-1]]

    if len(labels) > 0:
        labels = np.array(labels)
        ground_cls = labels[:, 0]
        ground_box = labels[:, 1:]
    else:
        ground_cls = []
        ground_box = []
    
    return ground_cls, ground_box

In [59]:
def precision_recall(predictions, ground_truths, iou_treshhold = 0.5):
    TP = FP = 0
    total_gt = len(ground_cls)
    detected = []

    for pred_cls, pred_box in predictions:
        best_iou = 0
        best_gt_index = -1

        for i, (gt_cls, gt_box) in enumerate(ground_truths):
            if i in detected or pred_cls != gt_cls:
                continue
        
            current_iou = iou(pred_box, gt_box)

            if current_iou > best_iou:
                best_iou = current_iou
                best_gt_index = i

        if best_iou >= iou_treshhold:
            TP += 1
            detected.append(best_gt_index)
        
        else:
            FP += 1

    precision = TP / (TP + FP) if TP + FP > 0 else 0
    recall = TP / total_gt if total_gt > 0 else 0
    return precision, recall, TP, FP, total_gt

In [49]:
# load yolo model
model = YOLO(PRM_BEST_MODEL_PATH)

# create empty list
records = list()

# iterate over images
for img_group, img_id, img_sst, img_path, lbl_path in sst_img_lbl:
    # get yolo results
    results = model(img_path)[0]

    # get predictions and true labels
    prediction_cls, prediction_box = get_predictions(results)
    ground_cls, ground_box = get_ground_truths(lbl_path)

    # get metrics
    precision, recall = precision_recall(predictions = zip(prediction_cls, prediction_box), 
                                         ground_truths = zip(ground_cls, ground_box), 
                                         iou_treshhold = 0.5)

    # save record
    records.append({'group': img_group,
                    'image_id': img_id,
                    'subset': img_sst,
                    'precision': precision,
                    'recall': recall})

# convert into pandas dataframe
records = pd.DataFrame(records)


image 1/1 /home/rodari78/tesis/CNN_bike_lanes/app/datasets/lima_bike_lanes_subsets/images/train/img_00000.png: 640x640 (no detections), 7.3ms
Speed: 1.0ms preprocess, 7.3ms inference, 0.4ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 /home/rodari78/tesis/CNN_bike_lanes/app/datasets/lima_bike_lanes_subsets/images/train/img_00005.png: 640x640 1 D20 - Alligator Crack, 6.0ms
Speed: 0.9ms preprocess, 6.0ms inference, 1.1ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 /home/rodari78/tesis/CNN_bike_lanes/app/datasets/lima_bike_lanes_subsets/images/train/img_00006.png: 640x640 1 D20 - Alligator Crack, 9.2ms
Speed: 1.0ms preprocess, 9.2ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 /home/rodari78/tesis/CNN_bike_lanes/app/datasets/lima_bike_lanes_subsets/images/train/img_00007.png: 640x640 1 D20 - Alligator Crack, 8.9ms
Speed: 1.0ms preprocess, 8.9ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 /home/rod

In [58]:
records[(records['precision'] != 0) & (records['recall'] != 0)].groupby(['group', 'subset'], as_index = False)\
                                                               .agg(mAP = ('precision', 'mean'))

group subset       mAP
0   Grupo_000000_000499   test  0.388425
1   Grupo_000000_000499  train  0.430577
2   Grupo_000000_000499    val  0.453416
3   Grupo_000500_000999   test  0.568615
4   Grupo_000500_000999  train  0.505206
5   Grupo_000500_000999    val  0.712745
6   Grupo_001000_001999   test  0.609713
7   Grupo_001000_001999  train  0.576405
8   Grupo_001000_001999    val  0.706829
9   Grupo_002000_002999   test  0.671981
10  Grupo_002000_002999  train  0.681851
11  Grupo_002000_002999    val  0.765152
12  Grupo_003000_003999   test  0.647778
13  Grupo_003000_003999  train  0.573625
14  Grupo_003000_003999    val  0.661574
15  Grupo_004000_004499   test  0.601567
16  Grupo_004000_004499  train  0.637771
17  Grupo_004000_004499    val  0.563889
18  Grupo_004500_004999   test  0.700820
19  Grupo_004500_004999  train  0.744980
20  Grupo_004500_004999    val  0.780303
21  Grupo_005000_005499   test  0.724510
22  Grupo_005000_005499  train  0.787105
23  Grupo_005000_005499    val  0.751111
24  Grupo_005500_005999   test  0.575309
25  Grupo_005500_005999  train  0.638571
26  Grupo_005500_005999    val  0.541667
27  Grupo_006000_006499   test  0.719697
28  Grupo_006000_006499  train  0.762572
29  Grupo_006000_006499    val  0.812500
30  Grupo_006500_006999   test  0.613622
31  Grupo_006500_006999  train  0.602203
32  Grupo_006500_006999    val  0.560606
33  Grupo_007000_007499   test  0.724667
34  Grupo_007000_007499  train  0.684676
35  Grupo_007000_007499    val  0.645833
36  Grupo_007500_007999   test  0.500000
37  Grupo_007500_007999  train  0.678066
38  Grupo_007500_007999    val  0.750000
39  Grupo_008000_008499   test  0.666667
40  Grupo_008000_008499  train  0.676437
41  Grupo_008000_008499    val  1.000000
42  Grupo_008500_008999   test  0.766667
43  Grupo_008500_008999  train  0.736520
44  Grupo_008500_008999    val  0.666667
45  Grupo_009000_009499   test  0.725379
46  Grupo_009000_009499  train  0.720438
47  Grupo_009000_009499    val  0.618056
48  Grupo_009500_009999   test  0.928571
49  Grupo_009500_009999  train  0.808664
50  Grupo_009500_009999    val  0.928571
51  Grupo_014500_014999   test  0.711224
52  Grupo_014500_014999  train  0.577790
53  Grupo_014500_014999    val  0.454545
54  Grupo_015000_015499   test  0.876812
55  Grupo_015000_015499  train  0.865686
56  Grupo_015000_015499    val  0.881283

In [85]:
precision_recall(predictions = zip(predictions_cls, predictions_box),
                 ground_truths = zip(ground_cls, ground_box))

(0.25, 0.3333333333333333)

In [83]:
precision, recall

(0.75, 1.0)

In [66]:
precision

0.75

In [67]:
recall

1.0

In [68]:
predictions

array([[    0.47144,     0.51986,    0.092171,    0.034474],
       [   0.056128,     0.49701,     0.11096,    0.030359],
       [    0.63074,     0.53439,     0.23245,    0.025128],
       [     0.3765,     0.51844,    0.098224,    0.031325]], dtype=float32)

In [59]:
ground_truths

array([[    0.47258,     0.52091,     0.10316,    0.038104],
       [   0.058086,     0.49861,     0.10502,    0.021375],
       [    0.65149,     0.53299,     0.27509,    0.032528]])

In [50]:
classes_real

array([          3,           3,           1])

In [47]:
labels

array([[          3,     0.47258,     0.52091,     0.10316,    0.038104],
       [          3,    0.058086,     0.49861,     0.10502,    0.021375],
       [          1,     0.65149,     0.53299,     0.27509,    0.032528]])

In [42]:
classes_real

NameError: name 'classes_real' is not defined

In [40]:
labels

['3 0.47258364312267653 0.5209107806691451 0.10315985130111527 0.03810408921933095',
 '3 0.058085501858736066 0.4986059479553903 0.1050185873605948 0.021375464684014887',
 '1 0.6514869888475836 0.5329925650557621 0.275092936802974 0.032527881040892194']

In [32]:
results.boxes.xyxy.cpu().numpy()

array([[     272.23,      321.68,      331.22,      343.74],
       [    0.41355,      308.37,       71.43,       327.8],
       [     329.29,      333.97,      478.06,      350.05],
       [     209.53,      321.78,      272.39,      341.83]], dtype=float32)

In [28]:
results.boxes.xywh

tensor([[301.7246, 332.7101,  58.9893,  22.0632],
        [ 35.9218, 318.0856,  71.0165,  19.4298],
        [403.6714, 342.0078, 148.7677,  16.0820],
        [240.9578, 331.8045,  62.8634,  20.0483]], device='cuda:0')

In [3]:
# load weights
model = YOLO(PRM_BEST_MODEL_PATH)
if os.path.exists(PRM_PREDICTION_NAME_PATH): shutil.rmtree(PRM_PREDICTION_NAME_PATH)
# validate on testing set (Lima bikelanes) with yolo
results = model.predict(source = 'datasets/lima_bike_lanes/images/test',
                        data = 'yaml/test.yaml',
                        name = PRM_PREDICTION_NAME,
                        imgsz = 640, 
                        save = True, 
                        save_txt = True,
                        show = False)



WARNING ⚠️ inference results will accumulate in RAM unless `stream=True` is passed, causing potential out-of-memory
errors for large sources or long-running streams and videos. See https://docs.ultralytics.com/modes/predict/ for help.

Example:
    results = model(source=..., stream=True)  # generator of Results objects
    for r in results:
        boxes = r.boxes  # Boxes object for bbox outputs
        masks = r.masks  # Masks object for segment masks outputs
        probs = r.probs  # Class probabilities for classification outputs

image 1/11000 /home/rodari78/tesis/CNN_bike_lanes/app/datasets/lima_bike_lanes/images/test/img_00000.png: 640x640 (no detections), 8.4ms
image 2/11000 /home/rodari78/tesis/CNN_bike_lanes/app/datasets/lima_bike_lanes/images/test/img_00001.png: 640x640 (no detections), 7.9ms
image 3/11000 /home/rodari78/tesis/CNN_bike_lanes/app/datasets/lima_bike_lanes/images/test/img_00002.png: 640x640 (no detections), 8.8ms
image 4/11000 /home/rodari78/tesis/CNN_bike_l